In [1]:
from dotenv import load_dotenv
import json

load_dotenv()

True

# Tool Schema Tests

In [ ]:
from typing import Any

from anthropic_agent.tools import ToolRegistry, tool


@tool
def get_weather(location: str, unit: str = "celsius") -> str:
    """Get the current weather in a given location.
    
    This function retrieves weather information for the specified location
    and returns it in the requested temperature unit.
    
    Args:
        location: The city and state, e.g. "San Francisco, CA"
        unit: The unit of temperature, either "celsius" or "fahrenheit"
    
    Returns:
        String describing the current weather
    """
    # Mock implementation
    return f"The weather in {location} is 22°{unit[0].upper()}"

@tool
def plan_travel_itinerary(
    travelers: list[dict[str, str]],
    destination: str,
    start_date: str,
    end_date: str,
    preferences: dict[str, Any] | None = None,
) -> str:
    """Plan a multi-day travel itinerary.
    
    This tool accepts structured traveler information along with
    trip preferences and returns a concise summary. It showcases
    nested objects and optional parameters in the schema.
    
    Args:
        travelers: List of traveler profiles including name and role
        destination: Target city or country for the itinerary
        start_date: Trip start in ISO format (YYYY-MM-DD)
        end_date: Trip end in ISO format (YYYY-MM-DD)
        preferences: Optional mapping of preference category to value
    
    Returns:
        String summary describing the generated itinerary
    """
    traveler_list = ", ".join(
        f"{traveler['name']} ({traveler.get('role', 'guest')})"
        for traveler in travelers
    )
    pref_summary = (
        ", ".join(f"{key}={value}" for key, value in preferences.items())
        if preferences
        else "standard preferences"
    )
    return (
        f"Trip to {destination} from {start_date} to {end_date} for "
        f"{len(travelers)} traveler(s): {traveler_list}. Preferences: {pref_summary}."
    )


registry = ToolRegistry()
registry.register_tools([get_weather, plan_travel_itinerary])
print("Registered tools:", [schema["name"] for schema in registry.get_schemas()])

Registered tools: ['get_weather', 'plan_travel_itinerary']


## Export as OpenAI Format

In [3]:
import json

openai_tool_payload = registry.get_schemas(schema_type="openai")

print(json.dumps(openai_tool_payload, indent=2))

[
  {
    "type": "function",
    "function": {
      "name": "get_weather",
      "description": "Get the current weather in a given location.\n\nThis function retrieves weather information for the specified location\nand returns it in the requested temperature unit.",
      "parameters": {
        "type": "object",
        "properties": {
          "location": {
            "type": "string",
            "description": "The city and state, e.g. \"San Francisco, CA\""
          },
          "unit": {
            "type": "string",
            "nullable": true,
            "description": "The unit of temperature, either \"celsius\" or \"fahrenheit\""
          }
        },
        "required": [
          "location"
        ]
      }
    }
  },
  {
    "type": "function",
    "function": {
      "name": "plan_travel_itinerary",
      "description": "Plan a multi-day travel itinerary.\n\nThis tool accepts structured traveler information along with\ntrip preferences and returns a concise su

## Export as Anthropic Format

In [4]:
import json

anthropic_tool_schemas = registry.get_schemas()
print(json.dumps(anthropic_tool_schemas, indent=2))

[
  {
    "name": "get_weather",
    "description": "Get the current weather in a given location.\n\nThis function retrieves weather information for the specified location\nand returns it in the requested temperature unit.",
    "input_schema": {
      "type": "object",
      "properties": {
        "location": {
          "type": "string",
          "description": "The city and state, e.g. \"San Francisco, CA\""
        },
        "unit": {
          "type": "string",
          "nullable": true,
          "description": "The unit of temperature, either \"celsius\" or \"fahrenheit\""
        }
      },
      "required": [
        "location"
      ]
    }
  },
  {
    "name": "plan_travel_itinerary",
    "description": "Plan a multi-day travel itinerary.\n\nThis tool accepts structured traveler information along with\ntrip preferences and returns a concise summary. It showcases\nnested objects and optional parameters in the schema.",
    "input_schema": {
      "type": "object",
      "

# Basic Agent with Tools

In [3]:
from anthropic_agent.database import FilesystemBackend, SQLBackend

In [4]:
import os
sql_backend = SQLBackend(
    connection_string=os.getenv("DATABASE_URL")
)

In [5]:
file_backend = FilesystemBackend(
    base_path="./test_data"
)

In [6]:
import asyncio

from anthropic_agent.core import AnthropicAgent
from anthropic_agent.tools import SAMPLE_TOOL_FUNCTIONS

agent = AnthropicAgent(
        system_prompt="You are a helpful assistant that should help the user with their questions.",
        model="claude-sonnet-4-5",
        tools=SAMPLE_TOOL_FUNCTIONS,
        db_backend=sql_backend,
        # db_backend=file_backend
    )

In [7]:
agent_uuid = agent.agent_uuid
print(agent_uuid)

332ce36b-520f-4baf-bb12-18a34a9dace1


In [8]:
print(agent)
# print(json.dumps(agent.tool_schemas, indent=2))

{
  "agent_uuid": "332ce36b-520f-4baf-bb12-18a34a9dace1",
  "system_prompt": "You are a helpful assistant that should help the user with their questions.",
  "model": "claude-sonnet-4-5",
  "max_steps": 50,
  "thinking_tokens": 0,
  "max_tokens": 2048,
  "stream_meta_history_and_tool_results": false,
  "beta_headers": [],
  "container_id": null,
  "messages_count": 0,
  "conversation_history_count": 0,
  "agent_logs_count": 0,
  "max_retries": 5,
  "base_delay": 1.0,
  "api_kwargs": {},
  "formatter": "xml",
  "compactor": null,
  "memory_store": null,
  "final_answer_check": false,
  "db_backend": "SQLBackend",
  "tools": [
    "add",
    "subtract",
    "multiply",
    "divide"
  ]
}


In [9]:
prompt = "What is 5 + (10 * 2)?"

## Running w/o queue

In [6]:
_res_wo_queue = agent.run(
    prompt=prompt,
)
res_wo_queue = await _res_wo_queue

In [7]:
print(res_wo_queue)

{
  "final_message": "ParsedBetaMessage(id='msg_012WphmLkdCcVnJ9eKxs1nKv', container=None, content=[ParsedBetaTextBlock(citations=None, text='The answer is **25**.\\n\\nTo break it down:\\n- 10 * 2 = 20\\n- 5 + 20 = 25', type='text', parsed_output=None)], context_management=None, model='claude-sonnet-4-5-20250929', role='assistant', stop_reason='end_turn', stop_sequence=None, type='message', usage=BetaUsage(cache_creation=BetaCacheCreation(ephemeral_1h_input_tokens=0, ephemeral_5m_input_tokens=0), cache_creation_input_tokens=0, cache_read_input_tokens=0, input_tokens=1208, output_tokens=39, server_tool_use=None, service_tier='standard'))",
  "conversation_history": [
    {
      "role": "user",
      "content": [
        {
          "type": "text",
          "text": "What is 5 + (10 * 2)?"
        }
      ]
    },
    {
      "content": [
        {
          "text": "I need to calculate 5 + (10 * 2) following the order of operations (multiplication first, then addition).\n\nLet me brea

In [8]:
print(res_wo_queue.final_message.content[0].text)

The answer is **25**.

To break it down:
- 10 * 2 = 20
- 5 + 20 = 25


## Running with Queue

### XML Formatter

In [10]:
queue: asyncio.Queue[str | None] = asyncio.Queue()

async def print_queue() -> None:
        while True:
            chunk = await queue.get()
            if chunk is None:
                break
            print(chunk, end="", flush=True)
            queue.task_done()

printer = asyncio.create_task(print_queue())

result = await agent.run(prompt, queue)

await queue.put(None)  # signal printer to stop
await printer

<content-block:text>I need to calculate 5 + (10 * 2). Following the order of operations, I'll first multiply 10 * 2, then add 5 to that result.
</content-block:text><content-block:tool_call>
{
  "type": "tool_use",
  "id": "toolu_01DDRU5ocrjQnMJhtyumgFjo",
  "name": "multiply",
  "input": {
    "a": 10,
    "b": 2
  }
}
</content-block:tool_call><content-block:tool_call>
{
  "type": "tool_use",
  "id": "toolu_01BCsHd2tkf79Rcm9sY6qtfy",
  "name": "add",
  "input": {
    "a": 5,
    "b": 20
  }
}
</content-block:tool_call><content-block:text>The answer is **25**.

Here's how it breaks down:
- First: 10 * 2 = 20
- Then: 5 + 20 = 25
</content-block:text>

#### Agent Resume

In [11]:
import nest_asyncio
nest_asyncio.apply()

In [12]:
agent2 = AnthropicAgent(
        agent_uuid=agent_uuid,
        tools=SAMPLE_TOOL_FUNCTIONS,
        db_backend=sql_backend,
        # db_backend=file_backend
    )
print(agent2.agent_uuid)

332ce36b-520f-4baf-bb12-18a34a9dace1


In [13]:
print(agent2)
prompt2 = "What did you do before? Explain in detail."

{
  "agent_uuid": "332ce36b-520f-4baf-bb12-18a34a9dace1",
  "system_prompt": "You are a helpful assistant that should help the user with their questions.",
  "model": "claude-sonnet-4-5",
  "max_steps": 50,
  "thinking_tokens": 0,
  "max_tokens": 2048,
  "stream_meta_history_and_tool_results": false,
  "beta_headers": [],
  "container_id": null,
  "messages_count": 6,
  "conversation_history_count": 0,
  "agent_logs_count": 0,
  "max_retries": 5,
  "base_delay": 1.0,
  "api_kwargs": {},
  "formatter": "xml",
  "compactor": null,
  "memory_store": null,
  "final_answer_check": false,
  "db_backend": "SQLBackend",
  "tools": [
    "add",
    "subtract",
    "multiply",
    "divide"
  ]
}


In [14]:
queue2: asyncio.Queue[str | None] = asyncio.Queue()

async def print_queue() -> None:
        while True:
            chunk = await queue2.get()
            if chunk is None:
                break
            print(chunk, end="", flush=True)
            queue2.task_done()

printer2 = asyncio.create_task(print_queue())

result2 = await agent2.run(prompt2, queue2)

await queue2.put(None)  # signal printer to stop
await printer2

<content-block:text>I solved the mathematical expression **5 + (10 * 2)** by following the correct order of operations (also known as PEMDAS - Parentheses, Exponents, Multiplication/Division, Addition/Subtraction).

Here's what I did in detail:

1. **Analyzed the expression**: I recognized that the expression contained both multiplication and addition, so I needed to follow the order of operations where multiplication must be performed before addition.

2. **First calculation - Multiplication**: 
   - I called the `multiply` function with parameters a=10 and b=2
   - This calculated 10 × 2 = 20

3. **Second calculation - Addition**:
   - Once I received the result of 20 from the multiplication, I then called the `add` function
   - I used a=5 (the original number outside the parentheses) and b=20 (the result from the multiplication)
   - This calculated 5 + 20 = 25

4. **Made the calls sequentially**: I couldn't make both function calls at the same time because the second calculation (

### Raw formatter

In [10]:
queue2: asyncio.Queue[str | None] = asyncio.Queue()

async def print_queue() -> None:
        while True:
            chunk = await queue2.get()
            if chunk is None:
                break
            print(chunk, end="\n", flush=True)
            queue2.task_done()

printer2 = asyncio.create_task(print_queue())

result2 = await agent.run(prompt, queue2, "raw")

await queue2.put(None)  # signal printer to stop
await printer2

{"message":{"id":"msg_01NC5kRQJNXZgXoCdBiVTt6c","container":null,"content":[],"context_management":null,"model":"claude-sonnet-4-5-20250929","role":"assistant","stop_reason":null,"stop_sequence":null,"type":"message","usage":{"cache_creation":{"ephemeral_1h_input_tokens":0,"ephemeral_5m_input_tokens":0},"cache_creation_input_tokens":0,"cache_read_input_tokens":0,"input_tokens":1542,"output_tokens":8,"server_tool_use":null,"service_tier":"standard"}},"type":"message_start"}
{"content_block":{"citations":null,"text":"","type":"text"},"index":0,"type":"content_block_start"}
{"delta":{"text":"I need to calculate 5 +","type":"text_delta"},"index":0,"type":"content_block_delta"}
{"delta":{"text":" (10 * 2) following","type":"text_delta"},"index":0,"type":"content_block_delta"}
{"delta":{"text":" the order of operations (multiplication first,","type":"text_delta"},"index":0,"type":"content_block_delta"}
{"delta":{"text":" then addition).\n\nLet me break this","type":"text_delta"},"index":0,"t

/Users/aurosoni/Documents/AI Forge/Repos/anthropic_agent/.venv/lib/python3.12/site-packages/pydantic/main.py:528: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `ParsedBetaTextBlock[TypeVar]` - serialized value may not be as expected [field_name='content', input_value=ParsedBetaTextBlock(citat...xt', parsed_output=None), input_type=ParsedBetaTextBlock])
  PydanticSerializationUnexpectedValue(Expected `BetaThinkingBlock` - serialized value may not be as expected [field_name='content', input_value=ParsedBetaTextBlock(citat...xt', parsed_output=None), input_type=ParsedBetaTextBlock])
  PydanticSerializationUnexpectedValue(Expected `BetaRedactedThinkingBlock` - serialized value may not be as expected [field_name='content', input_value=ParsedBetaTextBlock(citat...xt', parsed_output=None), input_type=ParsedBetaTextBlock])
  PydanticSerializationUnexpectedValue(Expected `BetaToolUseBlock` - serialized value may not be as expected [field_name='conten

{"message":{"id":"msg_01PqStfDrrHzRygs2joMLJQR","container":null,"content":[],"context_management":null,"model":"claude-sonnet-4-5-20250929","role":"assistant","stop_reason":null,"stop_sequence":null,"type":"message","usage":{"cache_creation":{"ephemeral_1h_input_tokens":0,"ephemeral_5m_input_tokens":0},"cache_creation_input_tokens":0,"cache_read_input_tokens":0,"input_tokens":1685,"output_tokens":24,"server_tool_use":null,"service_tier":"standard"}},"type":"message_start"}
{"content_block":{"id":"toolu_0143nRmePSm4TGDGzsAwgvhE","input":{},"name":"add","type":"tool_use","caller":null},"index":0,"type":"content_block_start"}
{"delta":{"partial_json":"","type":"input_json_delta"},"index":0,"type":"content_block_delta"}
{"delta":{"partial_json":"{\"a\": 5","type":"input_json_delta"},"index":0,"type":"content_block_delta"}
{"delta":{"partial_json":", \"","type":"input_json_delta"},"index":0,"type":"content_block_delta"}
{"delta":{"partial_json":"b\": 20}","type":"input_json_delta"},"index"

In [11]:
result2.__dict__

{'final_message': ParsedBetaMessage(id='msg_01DTd2hxPKAcTD2PrDpErBq1', container=None, content=[ParsedBetaTextBlock(citations=None, text='The answer is **25**.\n\nTo break it down:\n- 10 * 2 = 20\n- 5 + 20 = 25', type='text', parsed_output=None)], context_management=None, model='claude-sonnet-4-5-20250929', role='assistant', stop_reason='end_turn', stop_sequence=None, type='message', usage=BetaUsage(cache_creation=BetaCacheCreation(ephemeral_1h_input_tokens=0, ephemeral_5m_input_tokens=0), cache_creation_input_tokens=0, cache_read_input_tokens=0, input_tokens=1766, output_tokens=39, server_tool_use=None, service_tier='standard')),
 'conversation_history': [{'role': 'user',
   'content': [{'type': 'text', 'text': 'What is 5 + (10 * 2)?'}]},
  {'content': [{'text': 'I need to calculate 5 + (10 * 2) following the order of operations (multiplication first, then addition).\n\nLet me break this down:\n1. First: 10 * 2\n2. Then: 5 + (result from step 1)',
     'type': 'text'},
    {'id': 'too

In [13]:
print(result2.final_message.content[0].text)

The answer is **25**.

To break it down:
- 10 * 2 = 20
- 5 + 20 = 25


# Agent With Server Tools

In [3]:
from datetime import datetime
from anthropic_agent import AnthropicAgent
today_date = datetime.now().strftime("%Y-%m-%d")

SYSTEM_PROMPT = f"""Today's date is {today_date}.
You are a helpful financial and business analyst assistant. 
You are tasked with answering questions about Paytm, an Indian fintech company. 
Provide clear, concise, and accurate answers based on the question asked.
If you don't have enough information to answer accurately, say so."""

agent = AnthropicAgent(
    system_prompt=SYSTEM_PROMPT,
    model="claude-sonnet-4-5",
    server_tools=[{
        "type": "code_execution_20250825",
        "name": "code_execution"
    },
    {
        "type": "web_search_20250305",
        "name": "web_search",
        "max_uses": 50
    },
    {
        "type": "web_fetch_20250910",
        "name": "web_fetch",
        "max_uses": 50
    }],
    beta_headers=["code-execution-2025-08-25", "web-fetch-2025-09-10", "files-api-2025-04-14", "context-management-2025-06-27"],
    context_management={
        "edits": [
            {
                "type": "clear_tool_uses_20250919",
                # Trigger clearing when threshold is exceeded
                "trigger": {
                    "type": "input_tokens",
                    "value": 30000
                },
                # Number of tool uses to keep after clearing
                "keep": {
                    "type": "tool_uses",
                    "value": 3
                },
                # Optional: Clear at least this many tokens
                "clear_at_least": {
                    "type": "input_tokens",
                    "value": 5000
                },
                # Exclude these tools from being cleared
                "exclude_tools": ["web_search"]
            }
        ]
    }
)

In [4]:
agent_uuid = agent.agent_uuid
print(agent_uuid)

9352ddba-f965-4e0b-aab3-e90ba6fc38df


In [5]:
print(agent)

{
  "agent_uuid": "9352ddba-f965-4e0b-aab3-e90ba6fc38df",
  "system_prompt": "Today's date is 2025-12-05.\nYou are a helpful financial and business analyst assistant. \nYou are tasked with answering questions about Paytm, an Indian fintech company. \nProvide clear, concise, and accurate answers based on the question asked.\nIf you don't have enough information to answer accurately, say so.",
  "model": "claude-sonnet-4-5",
  "max_steps": 50,
  "thinking_tokens": 0,
  "max_tokens": 2048,
  "stream_meta_history_and_tool_results": false,
  "beta_headers": [
    "code-execution-2025-08-25",
    "web-fetch-2025-09-10",
    "files-api-2025-04-14",
    "context-management-2025-06-27"
  ],
  "container_id": null,
  "messages_count": 0,
  "conversation_history_count": 0,
  "agent_logs_count": 0,
  "max_retries": 5,
  "base_delay": 1.0,
  "api_kwargs": {
    "context_management": {
      "edits": [
        {
          "type": "clear_tool_uses_20250919",
          "trigger": {
            "type":

In [13]:
def collate_final_text(message) -> str:
    """
    Collate all text blocks after the last server tool use/result block.
    
    Args:
        message: The ParsedBetaMessage (e.g., result.final_message)
        
    Returns:
        Concatenated text from all text blocks after the last tool block
    """
    
    if not message or not message.content:
            return ""

    start_index = 0
    # Find the index of the last tool_use block, if any
    for i, block in enumerate(message.content):
        if getattr(block, 'type', '') in ['server_tool_use', 'web_search_tool_result', 'tool_use', 'tool_result']:
            start_index = i + 1
    
    full_text = []
    for block in message.content[start_index:]:
        # Check if block is a text block (standard or beta)
        if hasattr(block, 'text') and getattr(block, 'type', '') == 'text':
            full_text.append(block.text)
    
    return "".join(full_text)

In [7]:
# prompt = "Summarize Paytm’s latest quarterly (Q2 FY 2026) performance and key drivers"
# prompt = "Compare Paytm's latest quarterly (Q2 FY 2026) performance with Q2 FY 2025 performance"
prompt = "What is the base, adjusted, normalized ebitda for paytm in FY25? Mention the formula used for calculation."

In [8]:
_res_wo_queue = agent.run(
    prompt=prompt,
)
res_wo_queue = await _res_wo_queue

/Users/aurosoni/Documents/AI Forge/Repos/anthropic_agent/.venv/lib/python3.12/site-packages/pydantic/main.py:464: UserWarning: Pydantic serializer warnings:
  PydanticSerializationUnexpectedValue(Expected `literal['text']` - serialized value may not be as expected [field_name='type', input_value='web_fetch_tool_result', input_type=str])
  PydanticSerializationUnexpectedValue(Expected `BetaThinkingBlock` - serialized value may not be as expected [field_name='content', input_value=ParsedBetaTextBlock(citat...2udvhNKqPQuF8jJHftERQZ'), input_type=ParsedBetaTextBlock])
  PydanticSerializationUnexpectedValue(Expected `BetaRedactedThinkingBlock` - serialized value may not be as expected [field_name='content', input_value=ParsedBetaTextBlock(citat...2udvhNKqPQuF8jJHftERQZ'), input_type=ParsedBetaTextBlock])
  PydanticSerializationUnexpectedValue(Expected `BetaToolUseBlock` - serialized value may not be as expected [field_name='content', input_value=ParsedBetaTextBlock(citat...2udvhNKqPQuF8jJHf

In [14]:
res_wo_queue.final_message.__dict__

{'id': 'msg_01BfA3ZJcEwy2QmVjhLevYcb',
 'container': None,
 'content': [ParsedBetaTextBlock(citations=None, text="I'll search for Paytm's EBITDA information for FY25.", type='text', parsed_output=None),
  BetaServerToolUseBlock(id='srvtoolu_01XqkSxC5u8RKUFaaqMnRbHZ', caller=None, input={'query': 'Paytm EBITDA FY25 adjusted normalized'}, name='web_search', type='server_tool_use'),
  BetaWebSearchToolResultBlock(content=[BetaWebSearchResultBlock(encrypted_content='EswRCioIChgCIiQxMDM4NWM5Ny0wZjFhLTQwMWEtYTBlOS00YjhmMzI2ODFhNTQSDE2QslQDHt3I4GwkvhoMoZOPBJPvXmH3N43ZIjAd5r5bSq8juPIdUVimd2dyaWKJ0hjgWucOsQCIauAT8UXuVc/6EjJoRdIqSybXx3cqzxBSDpbGYUPtZGRwXE9zA0cDnHNlT5mywmWcvnMEcPMctA3ArBdHufz07j81lkbuzD/kEblI4eCH/tiBVen8RbFLZKZIOGHoAp0DeU09n6va07DBmc98jfsbFaF13KPirEgNhJJVm1YkTyeP/ghna/peoQc3nHXunZSuKy7rNDMlDm8wpfcLnySO+AeXCohcUkcfLiVTI54wAwPqWvcyCZdG7iUzPCfCZoHIGq0iwXfMQfTuk9cK7CMvHLinREcmHXA1xyGjWqxKk9hgA96jZ8X//SyuAtvl4fYp5g8MbRdJw0He6CvFh4SDO249HbZbebQupVaf112LCMRFU7keyB5MzcfMGlgsfeD9JPrEHMCzR

In [12]:
print(res_wo_queue.final_answer)

Based on the FY25 earnings release document, here is the information about Paytm's EBITDA for FY25:

## **Paytm EBITDA for FY25**

### **1. Base EBITDA (with ESOP cost):**
For the full year FY25, Paytm reported an EBITDA loss of ₹(2,506) Cr

**Formula:**
```
EBITDA = Revenue from Operations 
         - Direct Expenses (Payment processing charges + Promotional cashback & incentives + Other direct expenses)
         - Indirect Expenses (Marketing + Employee cost including ESOP + Software & cloud + Other indirect expenses)
```

### **2. Adjusted/Normalized EBITDA (EBITDA Before ESOP):**
For FY25, EBITDA Before ESOP was ₹(691) Cr with a margin of (10)%

For Q4 FY25 specifically, EBITDA Before ESOP was ₹81 Cr

**Formula:**
```
EBITDA Before ESOP = Revenue from Operations 
                    - Payment processing charges
                    - Promotional cashback & incentives  
                    - Other direct expenses
                    - Indirect Expenses (excluding ESOP cost)
         

In [15]:
final_text = collate_final_text(res_wo_queue.final_message)
print(final_text)

Based on the FY25 earnings release document, here is the information about Paytm's EBITDA for FY25:

## **Paytm EBITDA for FY25**

### **1. Base EBITDA (with ESOP cost):**
For the full year FY25, Paytm reported an EBITDA loss of ₹(2,506) Cr

**Formula:**
```
EBITDA = Revenue from Operations 
         - Direct Expenses (Payment processing charges + Promotional cashback & incentives + Other direct expenses)
         - Indirect Expenses (Marketing + Employee cost including ESOP + Software & cloud + Other indirect expenses)
```

### **2. Adjusted/Normalized EBITDA (EBITDA Before ESOP):**
For FY25, EBITDA Before ESOP was ₹(691) Cr with a margin of (10)%

For Q4 FY25 specifically, EBITDA Before ESOP was ₹81 Cr

**Formula:**
```
EBITDA Before ESOP = Revenue from Operations 
                    - Payment processing charges
                    - Promotional cashback & incentives  
                    - Other direct expenses
                    - Indirect Expenses (excluding ESOP cost)
         

# Agent with answer check

In [ ]:
import re

def validate_answer(answer: str) -> tuple[bool, str]:
    """
    Validate the answer based on the question asked.
    """
    text = answer
    
    if not text or not text.strip():
        return False, "Input text is empty"
    
    # Try to extract JSON from the text
    json_candidates = []
    
    # Method 1: Look for JSON in markdown code blocks
    code_block_pattern = r'```(?:json)?\s*(\{.*?\})\s*```'
    code_blocks = re.findall(code_block_pattern, text, re.DOTALL)
    json_candidates.extend(code_blocks)
    
    # Method 2: Look for JSON objects in the text (handle both {} and nested structures)
    json_object_pattern = r'\{[^{}]*(?:\{[^{}]*\}[^{}]*)*\}'
    json_objects = re.findall(json_object_pattern, text, re.DOTALL)
    json_candidates.extend(json_objects)
    
    # Method 3: Try the entire text as JSON
    json_candidates.append(text.strip())
    
    # Try to parse each candidate
    for candidate in json_candidates:
        candidate = candidate.strip()
        if not candidate:
            continue
            
        try:
            # Attempt to parse JSON
            parsed_json = json.loads(candidate)
            
            # Validate it's a dictionary
            if not isinstance(parsed_json, dict):
                continue
            
            # Check for required fields
            if 'name' not in parsed_json:
                continue
            
            if 'description' not in parsed_json:
                continue
            
            # Validate field types (should be strings or at least present)
            name_value = parsed_json['name']
            description_value = parsed_json['description']
            
            # Check if values are None
            if name_value is None or description_value is None:
                continue
            
            # Successfully found and validated JSON
            return True, json.dumps(parsed_json, ensure_ascii=False)
            
        except json.JSONDecodeError:
            # This candidate wasn't valid JSON, try next one
            continue
        except Exception as e:
            # Unexpected error, continue to next candidate
            continue
    
    # If we get here, no valid JSON was found
    return False, "No valid JSON with 'name' and 'description' fields found in text"


In [13]:
import asyncio

from anthropic_agent.core import AnthropicAgent

agent = AnthropicAgent(
        system_prompt="""
        You are a helpful assistant that should help the user with their questions.
        You should always return the answer in JSON format only with the following fields:
        - name
        - description
        """,
        model="claude-sonnet-4-5",
        final_answer_check=validate_answer,
        server_tools=[
        {
            "type": "web_search_20250305",
            "name": "web_search",
            "max_uses": 50
        },
        {
            "type": "web_fetch_20250910",
            "name": "web_fetch",
            "max_uses": 50
        }],
        beta_headers=["web-fetch-2025-09-10"],
    )

In [14]:
print(agent)
prompt = """
Search various products on Amazon in the category of gaming laptops.
Return any 5 results in JSON format with the following fields:
- name
- description
"""


{
  "agent_uuid": "c62f1766-f7b7-4ef9-8af8-73d04005b0d6",
  "system_prompt": "\n        You are a helpful assistant that should help the user with their questions.\n        You should always return the answer in JSON format only with the following fields:\n        - name\n        - description\n        ",
  "model": "claude-sonnet-4-5",
  "max_steps": 50,
  "thinking_tokens": 0,
  "max_tokens": 2048,
  "stream_meta_history_and_tool_results": false,
  "beta_headers": [
    "web-fetch-2025-09-10"
  ],
  "container_id": null,
  "messages_count": 0,
  "conversation_history_count": 0,
  "agent_logs_count": 0,
  "max_retries": 5,
  "base_delay": 1.0,
  "api_kwargs": {},
  "formatter": "xml",
  "compactor": null,
  "memory_store": null,
  "final_answer_check": true,
  "db_backend": "FilesystemBackend",
  "tools": []
}


In [15]:
queue: asyncio.Queue[str | None] = asyncio.Queue()

async def print_queue() -> None:
        while True:
            chunk = await queue.get()
            if chunk is None:
                break
            print(chunk, end="", flush=True)
            queue.task_done()

printer = asyncio.create_task(print_queue())

result = await agent.run(prompt, queue)

await queue.put(None)  # signal printer to stop
await printer

<meta_init data="{&quot;format&quot;: &quot;xml&quot;, &quot;user_query&quot;: &quot;\nSearch various products on Amazon in the category of gaming laptops.\nReturn any 5 results in JSON format with the following fields:\n- name\n- description\n&quot;, &quot;message_history&quot;: [{&quot;role&quot;: &quot;user&quot;, &quot;content&quot;: [{&quot;type&quot;: &quot;text&quot;, &quot;text&quot;: &quot;\nSearch various products on Amazon in the category of gaming laptops.\nReturn any 5 results in JSON format with the following fields:\n- name\n- description\n&quot;}]}], &quot;agent_uuid&quot;: &quot;c62f1766-f7b7-4ef9-8af8-73d04005b0d6&quot;, &quot;model&quot;: &quot;claude-sonnet-4-5&quot;}"></meta_init><content-block-text>I'll search for gaming laptops on Amazon and provide you with 5 results in JSON format.</content-block-text><content-block-tool_call id="srvtoolu_01V7wBoSB1dCJJCpgxRWauyQ" name="web_search" arguments="{&quot;query&quot;: &quot;gaming laptops Amazon&quot;}"></content-blo

In [16]:
result.__dict__

{'final_message': ParsedBetaMessage(id='msg_01RwosnhRPqe9osCWY6K1vyx', container=None, content=[ParsedBetaTextBlock(citations=None, text="I'll search for gaming laptops on Amazon and provide you with 5 results in JSON format.", type='text', parsed_output=None), BetaServerToolUseBlock(id='srvtoolu_01V7wBoSB1dCJJCpgxRWauyQ', caller=None, input={'query': 'gaming laptops Amazon'}, name='web_search', type='server_tool_use'), BetaWebSearchToolResultBlock(content=[BetaWebSearchResultBlock(encrypted_content='EpwKCioIChgCIiQxMDM4NWM5Ny0wZjFhLTQwMWEtYTBlOS00YjhmMzI2ODFhNTQSDIbB+KXQqWG4C39XYxoMIqABMGj0s7ucHcbTIjAYT9CBA7YPo1wtrz4HUA0waZYvcv4LgC3D8NH1n2lnP7Pv1lvm6I5kblBbp0vRdC8qnwminTvpSZGbNmbALZ9vmydi71zELJsuyk8bk80dDU++vpfS8xhLZ0/jcsleHCea1vzNEMSGexzn/WUEpkKl/yv2maTjck78WkHUMmUxKPZfO8Ib6Yp4GRgCP6rWhPw4Fh3Sfn6nH9W2fYmWaah+i/Jwv4CXkaG0LkyqwOeuqxNU8lD8sxiOOFA+3dtkXGYzKEFjiGfwKHuGKf/GYm8blJ+eXouYRFTP6CWEweiT1M5Owt4l/XKV0ptIt+SNSKJM4h+5bEJJzyModxE8n/0cBgnm7eCMRFO7ejNfgyaJO/zwPYjHM4ZzKOjxQxp3o0Mhu3O+Sq

In [17]:
print(validate_answer(result.final_answer))

(True, '{"name": "ASUS ROG Strix G16 (2025) Gaming Laptop", "description": "16\\" FHD+ 165Hz/3ms display, NVIDIA GeForce RTX 5060 Laptop GPU, Intel Core i7 Processor 14650HX, 16GB DDR5, 1TB Gen 4 SSD, Wi-Fi 7, Windows 11 Home. Features tri-fan technology with vapor chamber cooling, 360° RGB light bar, and ROG Intelligent Cooling for optimal gaming performance."}')


In [18]:
print(result.final_answer)

Based on my search results, here are 5 gaming laptops available on Amazon in JSON format:

```json
[
  {
    "name": "ASUS ROG Strix G16 (2025) Gaming Laptop",
    "description": "16\" FHD+ 165Hz/3ms display, NVIDIA GeForce RTX 5060 Laptop GPU, Intel Core i7 Processor 14650HX, 16GB DDR5, 1TB Gen 4 SSD, Wi-Fi 7, Windows 11 Home. Features tri-fan technology with vapor chamber cooling, 360° RGB light bar, and ROG Intelligent Cooling for optimal gaming performance."
  },
  {
    "name": "MSI Katana 15 HX Gaming Laptop",
    "description": "15.6\" QHD+ 165Hz display, Intel Core i9-14900HX processor, NVIDIA GeForce RTX 5070 with NVIDIA Blackwell architecture, 32GB DDR5, 1TB NVMe SSD, RGB keyboard, Windows 11 Home. Features Cooler Boost 5 cooling system and 4-zone RGB keyboard with highlighted WASD keys for competitive gaming."
  },
  {
    "name": "Lenovo Legion Pro 7i Gaming Laptop",
    "description": "16\" 2.5K WQXGA OLED display with 240Hz refresh rate, Intel Core Ultra 9 275HX processor

# File Generation Agent + Rerun on same Agent Instance

In [2]:
import asyncio
from anthropic_agent import AnthropicAgent

agent = AnthropicAgent(
        system_prompt="You are a helpful assistant that should help the user with their questions.",
        model="claude-sonnet-4-5",
        thinking_tokens=1024,
        max_tokens=64000,
        server_tools=[{
            "type": "code_execution_20250825",
            "name": "code_execution"
        }],
        beta_headers=["files-api-2025-04-14", "code-execution-2025-08-25"],
        file_backend="local"
        )

In [3]:
agent_uuid = agent.agent_uuid
print(agent_uuid)

6aefbd37-6fbc-4b2d-8ce5-19cce626c6e6


In [4]:
print(agent)

{
  "agent_uuid": "6aefbd37-6fbc-4b2d-8ce5-19cce626c6e6",
  "system_prompt": "You are a helpful assistant that should help the user with their questions.",
  "model": "claude-sonnet-4-5",
  "max_steps": 50,
  "thinking_tokens": 1024,
  "max_tokens": 64000,
  "stream_meta_history_and_tool_results": false,
  "beta_headers": [
    "files-api-2025-04-14",
    "code-execution-2025-08-25"
  ],
  "container_id": null,
  "messages_count": 0,
  "conversation_history_count": 0,
  "agent_logs_count": 0,
  "max_retries": 5,
  "base_delay": 1.0,
  "api_kwargs": {},
  "formatter": "xml",
  "compactor": null,
  "memory_store": null,
  "final_answer_check": false,
  "db_backend": "FilesystemBackend",
  "tools": []
}


In [5]:
prompt = {
    "role": "user",
    "content": [
        {
            "type": "text",
            "text": "Generate a sample invoice image for a hypothetical restuarant and return that image."
        },
    ]
}

In [6]:
queue: asyncio.Queue[str | None] = asyncio.Queue()

async def print_queue() -> None:
        while True:
            chunk = await queue.get()
            if chunk is None:
                break
            print(chunk, end="", flush=True)
            queue.task_done()

printer = asyncio.create_task(print_queue())

result = await agent.run(prompt, queue, "xml")

await queue.put(None)  # signal printer to stop
await printer

<content-block-thinking>The user wants me to generate a sample invoice image for a hypothetical restaurant. To do this, I'll need to:

1. Create a script (likely Python) that generates an invoice image
2. Use a library like PIL/Pillow to create the image
3. Save it to a temporary location first, then copy it to OUTPUT_DIR

Let me create a Python script that will generate a nice-looking restaurant invoice with typical elements like:
- Restaurant name and contact info
- Invoice number and date
- Table number
- Itemized list of food/drinks
- Subtotal, tax, and total
- Thank you message

I'll use PIL (Pillow) which should be available in the container.</content-block-thinking><content-block-text>I'll create a sample restaurant invoice image for you. Let me generate a professional-looking invoice with typical restaurant details.</content-block-text><content-block-tool_call id="srvtoolu_01Sx6MP3WAwgM1Mmig4ZXQ5L" name="text_editor_code_execution" arguments="{&quot;command&quot;: &quot;create&

In [7]:
result.conversation_history

[{'role': 'user',
  'content': [{'type': 'text',
    'text': 'Generate a sample invoice image for a hypothetical restuarant and return that image.'}]},
 {'content': [{'signature': 'EpgGCkYIChgCKkBz0IwhOXbx5p631GKz0L9Tf3+nqFWHfXo4TneCS39X3nKThTolu2MBar3/3ZKTROZjSg2et6oYQywtDREq8v2uEgyLDrzwTjtH8L4XgegaDG4zoirteTHUTdgV5yIwLlXMLxLgdfr3+32+w09Gu/JMSfReqRAZQaLknQLpSTUh8vdPRHRru8Q0SzG3NqUfKv8EJkXAIBpW5adN7n0wNWIPCrMlzHX7V/QtNg5MWZxg7qcOM17p72X3VnG1L4jU6fwe0/0xET5K1fNcvOrYCuujplQ03ZN1BUbfAprb/1nnt6VbcbvBspTxASwscjuZ+tjvOcnRR/hhZNbxFLboKstgxDMMDKJDo4T7DQwJzvPXKBtNbUMygb3uo5rBlyRim7kZTLuHnGRVHsTcHFFYdmJC601oFcXHFyXUKRQxDI/FlowqurKYvUIpma9MfG3vulwFnC19CiR3NB5lhhY5t2CNWFuqtcaqRJfBt2glvWSOm1PVs5D4/Zld51I29qY8u4oUaXikD+0jsDReosHppCXXcVOruMOJNQ7GFPqs4KWdFC1UtiWXfa4hwB9SD32ZLLb4f/isgZ5+A6Ew2GrAO6We4NdpiHHEVvTN2xcbW+JqpWcRQs5E8qUfBMvaanZvbXxIv3Riqi9Su4YNI+fL6sFoVV0yP74DORVmfYdCfLf1GmOOTH1vfu6HX6uYzogk4aeaBrm9mN1fot18KLn6NCcnAg9NJR4HTAOMqjffUPs6C9REBNqmlozOBvMleks/+ziaDgkmHCKfIG7e0RR6JAmusenGLbc6WNadiTI

In [8]:
result.generated_files

[{'file_id': 'file_011CVr8XKLKbV4iEkdMi7V5D',
  'filename': 'restaurant_invoice.png',
  'first_seen_step': 0,
  'created_at': '2025-12-07T02:48:41.937229',
  'last_seen_step': 0,
  'updated_at': '2025-12-07T02:48:41.937229',
  'storage_path': '/Users/aurosoni/Documents/AI Forge/Repos/anthropic_agent/agent-files/6aefbd37-6fbc-4b2d-8ce5-19cce626c6e6/file_011CVr8XKLKbV4iEkdMi7V5D_restaurant_invoice.png',
  'size': 67295,
  'timestamp': '2025-12-07T02:48:42.960383',
  'is_update': False,
  'storage_backend': 'local',
  'processed_at_step': 0}]

In [9]:
print(result.final_answer)

Perfect! I've generated a sample restaurant invoice image for you. The invoice includes:

**Restaurant Details:**
- Restaurant name: "The Golden Fork - Fine Dining Restaurant"
- Address and contact information

**Invoice Information:**
- Invoice number (#12345)
- Current date and time
- Table number (12), Server name (Maria), and number of guests (2)

**Menu Items:**
- Caesar Salad (x2)
- Grilled Salmon with Herbs
- Beef Tenderloin Steak
- Truffle Mushroom Risotto
- Garlic Bread
- House Red Wine (x2 glasses)
- Sparkling Water (x2)
- Tiramisu (x2)
- Espresso (x2)

**Financial Summary:**
- Itemized pricing for each item
- Subtotal
- 8% tax
- Total amount

The invoice has a professional layout with a clean design, including the restaurant's branding colors and a thank you message at the bottom. The image has been exported and is ready for your use!


## Followup run on same agent instance

**Expected Behavior**
- Maintains context (self.messages)
- Resets conversation history.
- Should maintain file registry and stream both files at the end.

In [10]:
prompt_2 = {
    "role": "user",
    "content": [
        {
            "type": "text",
            "text": "Reduce some items from the invoice (modify the same file_id) and also create another version of the\
                invoice with the values in INR only."
        },
    ]
}

In [11]:
queue_2: asyncio.Queue[str | None] = asyncio.Queue()

async def print_queue() -> None:
        while True:
            chunk = await queue_2.get()
            if chunk is None:
                break
            print(chunk, end="", flush=True)
            queue_2.task_done()

printer_2 = asyncio.create_task(print_queue())

result_2 = await agent.run(prompt_2, queue_2, "xml")

await queue_2.put(None)  # signal printer to stop
await printer_2

<content-block-thinking>The user wants me to:
1. Reduce some items from the invoice (modify the same file)
2. Create another version with values in INR only

I'll need to modify the Python script to:
1. Remove some items from the list
2. Save the modified USD version
3. Create a second version with INR currency

I'll keep the file at /tmp/generate_invoice.py and modify it to have fewer items, then create a second script for INR version.</content-block-thinking><content-block-text>I'll modify the invoice to have fewer items and create both USD and INR versions for you.</content-block-text><content-block-tool_call id="srvtoolu_01Fag8aFzP6nGZtb2dZBxuDG" name="text_editor_code_execution" arguments="{&quot;command&quot;: &quot;str_replace&quot;, &quot;path&quot;: &quot;/tmp/generate_invoice.py&quot;, &quot;old_str&quot;: &quot;# Menu items\nitems = [\n    (\&quot;Caesar Salad\&quot;, 2, 14.50),\n    (\&quot;Grilled Salmon with Herbs\&quot;, 1, 32.00),\n    (\&quot;Beef Tenderloin Steak\&quo

In [12]:
result_2.conversation_history

[{'role': 'user',
  'content': [{'type': 'text',
    'text': 'Reduce some items from the invoice (modify the same file_id) and also create another version of the                invoice with the values in INR only.'}]},
 {'content': [{'signature': 'EsQECkYIChgCKkApJqStEw7QsAodWIIqt2hTlO9SlBLGQiYceQWjCNwvuywA0Mj0e+XzcFwszleBv/UvtGvtseQv1Y68y7HClpDeEgxqwTgmiVZWsqJzC5saDJitYd8qrBEQpQc8uCIwsVdL2VEsL99Iuwao+EAu4JSCzKGQUqbw3AbsIxQWPxqHADrmEGPYL1kWb7JWKGFCKqsDEUdIZ2zuXJdGkYj2BtA/HOFUIWhBUqkZH89uNmwwyXUpRwtoG2S6iDwW2PCbDqWyrS5chPOgRPtmh2yhxm5EvjQEcgTTTngpgts/w2+ilGqfYIAx9ruoirLCH1SNw4aAVRl602PSsslqCqnW9Xxs4ibPXTt7k1X8C3xebcw2s1ekKzOkYcMXkP6HvuoNSpRuSdNxVnVErw0eQ36KkdP/eoHbHbdb1U63DFBUmIBv6UrKp23gAidQ3Ie+7S0Z8cqKXh+c/fqx5y31OQq3wzEDCICZOVWe0SMnpmtYsuq73Yn7VXRdD0t3cZdo0SEdQR/CV0nh4/oxwS8xdL3T+EgHVz2alOsCY+nrYeGXlp820oP41TzQfc906Xh1FQWwxwzcrqfBdyc/W8W4YQKho8r5qW3jR6qDVry1t7BYFouW8l1BJ3BIS0GKaukvNI6gKp5VODhJ2NCVA8n/fohgkUrUGOEgMUGcaafcq0JA8jEDokNZ8hqVT7IXicrcMBCuvufUS2Y2jB6ruRQYq8kzauhlyVdyovqA8JJG

In [13]:
result_2.generated_files

[{'file_id': 'file_011CVr8XKLKbV4iEkdMi7V5D',
  'filename': 'restaurant_invoice.png',
  'first_seen_step': 0,
  'created_at': '2025-12-07T02:48:41.937229',
  'last_seen_step': 0,
  'updated_at': '2025-12-07T02:48:41.937229',
  'storage_path': '/Users/aurosoni/Documents/AI Forge/Repos/anthropic_agent/agent-files/6aefbd37-6fbc-4b2d-8ce5-19cce626c6e6/file_011CVr8XKLKbV4iEkdMi7V5D_restaurant_invoice.png',
  'size': 67295,
  'timestamp': '2025-12-07T02:51:03.272784',
  'is_update': True,
  'storage_backend': 'local',
  'processed_at_step': 0,
  'previous_size': 67295},
 {'file_id': 'file_011CVr8hZeLJJionEoQyrA9a',
  'filename': 'restaurant_invoice.png',
  'first_seen_step': 0,
  'created_at': '2025-12-07T02:51:02.082836',
  'last_seen_step': 0,
  'updated_at': '2025-12-07T02:51:02.082836',
  'storage_path': '/Users/aurosoni/Documents/AI Forge/Repos/anthropic_agent/agent-files/6aefbd37-6fbc-4b2d-8ce5-19cce626c6e6/file_011CVr8hZeLJJionEoQyrA9a_restaurant_invoice.png',
  'size': 57662,
  'time

In [14]:
print(result_2.final_answer)

Perfect! I've created both invoice versions with reduced items:

**Changes Made:**

1. **Reduced Items** - Now the invoice includes only 5 items instead of 9:
   - Grilled Salmon with Herbs (1)
   - Beef Tenderloin Steak (1)
   - Garlic Bread (1)
   - House Red Wine - 2 glasses (2)
   - Tiramisu (1)

2. **USD Version** (`restaurant_invoice.png`):
   - Prices in US Dollars ($)
   - 8% sales tax
   - US address format
   - Server: Maria

3. **INR Version** (`restaurant_invoice_inr.png`):
   - Prices in Indian Rupees (₹)
   - 18% GST (standard restaurant tax in India)
   - Indian address (Mumbai)
   - Server: Priya
   - Payment methods include UPI and Paytm
   - Prices converted to INR (approximately 83 INR per USD)

Both invoice images have been exported and are ready for use!


# Agent with Image/File + Thinking + Tool Calls (Server + Client) + S3 File Backend + DB Storage Backend

In [2]:
test_image = "./currency_receipt_usd_jpy.png"
# Convert image to base64
import base64

with open(test_image, "rb") as image_file:
    base64_image = base64.b64encode(image_file.read()).decode('utf-8')

In [3]:
# Defining the tools
from anthropic_agent.tools import tool

@tool
def get_rate(source: str, target: str) -> str:
    '''
    Get the exchange rate from source to target currency.
    Args:
        source: The source currency code. It can be INR, USD, or JPY.
        target: The target currency code. It can be INR, USD, or JPY.
    Returns:
        A string describing the exchange rate from source to target currency
    '''
    # For testing: return fixed mock rates
    mock_rates = {
        ("INR", "USD"): 0.012,
        ("USD", "INR"): 83.1,
        ("INR", "JPY"): 1.5,
        ("JPY", "INR"): 66.7,
        ("USD", "JPY"): 110.0,
        ("JPY", "USD"): 0.0091,
    }
    return f"The exchange rate from {source} to {target} is {mock_rates[(source, target)]}"

In [36]:
import asyncio

from anthropic_agent import AnthropicAgent
from anthropic_agent.tools import SAMPLE_TOOL_FUNCTIONS
from anthropic_agent.file_backends import S3Backend
from anthropic_agent.database import SQLBackend
import os

file_backend = S3Backend(
    bucket="agent-files-bucket-3c8qbd",   
)
db_backend = SQLBackend(
    connection_string=os.getenv("DATABASE_URL")
)

agent = AnthropicAgent(
        system_prompt="You are a helpful assistant that should help the user with their questions.",
        model="claude-sonnet-4-5",
        thinking_tokens=1024,
        max_tokens=64000,
        tools=SAMPLE_TOOL_FUNCTIONS + [get_rate],
        server_tools=[{
            "type": "code_execution_20250825",
            "name": "code_execution"
        }],
        beta_headers=["files-api-2025-04-14", "code-execution-2025-08-25"],
        file_backend=file_backend,
        db_backend=db_backend
        )

In [37]:
agent_uuid = agent.agent_uuid
print(agent_uuid)

63bd00f7-9492-452e-8703-af1202b82a22


In [38]:
print(agent)

{
  "agent_uuid": "63bd00f7-9492-452e-8703-af1202b82a22",
  "system_prompt": "You are a helpful assistant that should help the user with their questions.",
  "model": "claude-sonnet-4-5",
  "max_steps": 50,
  "thinking_tokens": 1024,
  "max_tokens": 64000,
  "stream_meta_history_and_tool_results": false,
  "beta_headers": [
    "files-api-2025-04-14",
    "code-execution-2025-08-25"
  ],
  "container_id": null,
  "messages_count": 0,
  "conversation_history_count": 0,
  "agent_logs_count": 0,
  "max_retries": 5,
  "base_delay": 1.0,
  "api_kwargs": {},
  "formatter": "xml",
  "compactor": null,
  "memory_store": null,
  "final_answer_check": false,
  "db_backend": "SQLBackend",
  "tools": [
    "add",
    "subtract",
    "multiply",
    "divide",
    "get_rate"
  ]
}


In [39]:
prompt_1 = {
    "role": "user",
    "content": [
        {
            "type": "image",
            "source": {
                "type": "base64",
                "media_type": "image/png",
                "data": base64_image,
            },
        },
        {
            "type": "text",
            "text": "I paid the receipt in USD. What is the amount in INR?"
        },
    ]
}

In [40]:
# import logging

# logging.basicConfig(level=logging.INFO)  # or configure handlers as you prefer
# # logging.getLogger("anthropic_agent.src.core.agent").setLevel(logging.DEBUG)
# # logging.getLogger("anthropic_agent.src.core.retry").setLevel(logging.DEBUG)


In [41]:
queue: asyncio.Queue[str | None] = asyncio.Queue()

async def print_queue() -> None:
        while True:
            chunk = await queue.get()
            if chunk is None:
                break
            print(chunk, end="", flush=True)
            queue.task_done()

printer = asyncio.create_task(print_queue())

result = await agent.run(prompt_1, queue, "xml")

await queue.put(None)  # signal printer to stop
await printer

<meta_init data="{&quot;format&quot;: &quot;xml&quot;, &quot;user_query&quot;: &quot;{\&quot;role\&quot;: \&quot;user\&quot;, \&quot;content\&quot;: [{\&quot;type\&quot;: \&quot;image\&quot;, \&quot;source\&quot;: {\&quot;type\&quot;: \&quot;base64\&quot;, \&quot;media_type\&quot;: \&quot;image/png\&quot;, \&quot;data\&quot;: \&quot;...\&quot;}}, {\&quot;type\&quot;: \&quot;text\&quot;, \&quot;text\&quot;: \&quot;I paid the receipt in USD. What is the amount in INR?\&quot;}]}&quot;, &quot;message_history&quot;: [{&quot;role&quot;: &quot;user&quot;, &quot;content&quot;: [{&quot;type&quot;: &quot;image&quot;, &quot;source&quot;: {&quot;type&quot;: &quot;base64&quot;, &quot;media_type&quot;: &quot;image/png&quot;, &quot;data&quot;: &quot;...&quot;}}, {&quot;type&quot;: &quot;text&quot;, &quot;text&quot;: &quot;I paid the receipt in USD. What is the amount in INR?&quot;}]}], &quot;agent_uuid&quot;: &quot;63bd00f7-9492-452e-8703-af1202b82a22&quot;, &quot;model&quot;: &quot;claude-sonnet-4-5

In [42]:
result.conversation_history

[{'role': 'user',
  'content': [{'type': 'image',
    'source': {'type': 'base64',
     'media_type': 'image/png',
     'data': '...'}},
   {'type': 'text',
    'text': 'I paid the receipt in USD. What is the amount in INR?'}]},
 {'content': [{'signature': 'EsgDCkYIChgCKkC1zS5HE0VVgeQvGJyIynsdUIig/l9wCSPIDsP1qeinXJnvlVyNo/gu5NcFtN/a1Ol16V8JslXL/Fsyp/Y527U8EgxM7yzoScvWpqTWeOsaDGloKGZ7cmQcPrhOvSIwM+yHZ+ljj68eMHbrLcKRKBhz+AVYRtRZ4TyA0qd8Jl6tH7nRZkCf33NBy4Uppa2gKq8CuUyr/oGKkK1H7aO3rnKREDZC8W3+3o/Gpyy2IbNz+jK21YarIXqby6IHbCBQ2/f1jkP71KQ6hU7spv26J36pbONXBOOdU0VY8AZkhSBVzLBmGULXeVI53jhJUg8Iba5QS7P//KiU8S3W2QAg4zu0g039DCjnaFdWL/0qiYRt8MphsRu+TVK4SIkHhUK6Un6nk1klPIZDixDc+OepZf25+nwDSx0Z/eYUn37vqW5hwad18LCaRC6CKfU3mho+e9l5tqpkVFRyS/nwu+viBsvpY1msZ1GeQkNsumo8QStq3oJubz5zBhi0hG86bqAMcxqd+N27A5s9Q7zxFWyFRfP5hEPEuLVNZLINjYmE3J/0LnclHTtSeGAYIIUa7nytHvJniifN+VMfjQB2Dq6GTaGBGAE=',
    'thinking': 'The user paid in USD and wants to know the amount in INR. The total in USD is $38.44.\n\nI need to convert

In [43]:
result.generated_files

[]

In [44]:
print(result.final_answer)

**The amount in INR is ₹3,194.36**

Based on the current exchange rate of 1 USD = 83.1 INR, your total payment of $38.44 USD equals approximately **₹3,194.36 INR**.


In [45]:
prompt_2 = {
    "role": "user",
    "content": [
        {
            "type": "text",
            "text": "Now generate a recepit image for the amount of various\
                items in INR only. Export and return the image to me."
        }
    ]
}

In [46]:
queue_2: asyncio.Queue[str | None] = asyncio.Queue()

async def print_queue() -> None:
        while True:
            chunk = await queue_2.get()
            if chunk is None:
                break
            print(chunk, end="", flush=True)
            queue_2.task_done()

printer_2 = asyncio.create_task(print_queue())

result_2 = await agent.run(prompt_2, queue_2, "xml")

await queue_2.put(None)  # signal printer to stop
await printer_2

<meta_init data="{&quot;format&quot;: &quot;xml&quot;, &quot;user_query&quot;: &quot;{\&quot;role\&quot;: \&quot;user\&quot;, \&quot;content\&quot;: [{\&quot;type\&quot;: \&quot;text\&quot;, \&quot;text\&quot;: \&quot;Now generate a recepit image for the amount of various                items in INR only. Export and return the image to me.\&quot;}]}&quot;, &quot;message_history&quot;: [{&quot;role&quot;: &quot;user&quot;, &quot;content&quot;: [{&quot;type&quot;: &quot;text&quot;, &quot;text&quot;: &quot;Now generate a recepit image for the amount of various                items in INR only. Export and return the image to me.&quot;}]}], &quot;agent_uuid&quot;: &quot;63bd00f7-9492-452e-8703-af1202b82a22&quot;, &quot;model&quot;: &quot;claude-sonnet-4-5&quot;}"></meta_init><content-block-thinking>The user wants me to create a receipt image showing the items in INR only. I need to:
1. Convert each item's USD price to INR using the exchange rate of 83.1
2. Create a receipt image similar to 

In [47]:
result_2.conversation_history

[{'role': 'user',
  'content': [{'type': 'text',
    'text': 'Now generate a recepit image for the amount of various                items in INR only. Export and return the image to me.'}]},
 {'content': [{'signature': 'Eu0FCkYIChgCKkB3sVGfY8o2j0xDBpC0Ak58g5kOh9EGGJj4GahzYlVcEPgOpKQCH5zg+Zx4U6fZc0gz+uYN5w86z8UoTzVqsA0PEgyDnUF5HekS8yimkbUaDAeUwEPFyhDEHW+LZSIwQYkPC2u+vvlFstLbJ31ZQGsMLaeqWQUoF5BGdnI/QsgMrV6NY+H8oNPIv9fcgXuPKtQED23Pj0X90K71+kF5Y1lHedQXct6SBtiB5zGhYebcga5/voaruERmgJySqXeDhWHytxsd1bfXrQdjtphIuG7RLNjRPGUlWkJ7zwTAi4/vwdpl51+SetWa0baZXmdbmT5/U0DARMia3BNbCvHcZR+jFPV0+6yeF646toEFr/2KJRajp5A4bVvXXU0YB1dae1AkGTimwnodnA5MHJwxR8pmEt0yQN9tVTa6CVHEbt/3DYRPWlA5nPkmaWmVT98QAgNIJzOugphKIvpzA18KLYU/kfIzHKntMRFyKJaf8mhbn80xkzHnMgm05bKBPouOZN8ekg8lwlt8QhLF17F8/nOG2B+h3MDP2X/6ySSTnEeHUTbgPaxYqajMNyXMrA4TtWVSfioXkg+bhJ6cG+YCSpmOrkucTGbziURfMsY1NB6R9abvNz2YJxl0+TprzfWaM6EB9U+9NVhcBLQhGmEtSYQVHljMrVML3KSlZMHIehHUgFbrDr2OCAny/aXjwr0RgCFSLriJsA3ty+TSxkw09xyf5a1qketc33yVI52Ija6jujbe6pfXnRE0sSX0J8yB

In [48]:
result_2.generated_files

[{'file_id': 'file_011CVropdeAkLSN6Lo2iJr5J',
  'filename': 'receipt_inr.png',
  'first_seen_step': 0,
  'created_at': '2025-12-07T09:54:00.421213',
  'last_seen_step': 0,
  'updated_at': '2025-12-07T09:54:00.421213',
  'storage_location': 'https://agent-files-bucket-3c8qbd.s3.ap-south-1.amazonaws.com/agent-files/63bd00f7-9492-452e-8703-af1202b82a22/file_011CVropdeAkLSN6Lo2iJr5J_receipt_inr.png',
  'size': 42851,
  'timestamp': '2025-12-07T09:54:02.427705',
  'is_update': False,
  'storage_backend': 's3',
  's3_bucket': 'agent-files-bucket-3c8qbd',
  's3_key': 'agent-files/63bd00f7-9492-452e-8703-af1202b82a22/file_011CVropdeAkLSN6Lo2iJr5J_receipt_inr.png',
  'processed_at_step': 0}]

In [49]:
print(result_2.final_answer)

Perfect! I've created and exported your receipt image with all amounts in INR. 

**Receipt Summary (INR):**
- Coffee Beans 1kg: ₹1,537.35
- Green Tea 200g: ₹810.23
- Chocolate Bar: ₹248.47
- Imported Snacks: ₹598.32
- **Total: ₹3,194.36**

The receipt image has been generated and exported as **receipt_inr.png**. It includes all the items with their prices in Indian Rupees using the exchange rate of 1 USD = 83.1 INR.


In [50]:
await agent.drain_background_tasks()

{'total_tasks': 1, 'completed': 1, 'timed_out': 0, 'task_ids': []}

# Agent with Frontend Tools

In [2]:
from anthropic_agent.tools import tool

# Define a frontend tool - this will be executed by the browser, not the server
@tool(executor="frontend")
def user_confirm(message: str) -> str:
    """Ask the user for yes/no confirmation before proceeding with an action.
    
    Use this tool when you need explicit user approval before taking an action
    that could have significant consequences.
    
    Args:
        message: The confirmation message to display to the user, explaining
                what action requires their approval.
    
    Returns:
        "yes" if user confirms, "no" if user declines
    """
    pass  # Never executed server-side - runs in browser


# Define a backend tool - executed on server
@tool
def calculate(expression: str) -> str:
    """Evaluate a mathematical expression.
    
    Args:
        expression: A mathematical expression to evaluate (e.g., "2 + 2")
    
    Returns:
        The result of the calculation as a string
    """
    try:
        # Safe eval for simple math
        allowed = set("0123456789+-*/().% ")
        if all(c in allowed for c in expression):
            result = eval(expression)
            return f"Result: {result}"
        return "Error: Invalid expression"
    except Exception as e:
        return f"Error: {str(e)}"
    
# Verify tool executor attributes
print(f"user_confirm executor: {user_confirm.__tool_executor__}")
print(f"calculate executor: {calculate.__tool_executor__}")


user_confirm executor: frontend
calculate executor: backend


In [3]:
from anthropic_agent.core import AnthropicAgent

# Create agent with both backend and frontend tools
frontend_agent = AnthropicAgent(
    system_prompt="""You are a helpful assistant. When asked to perform calculations,
    use the calculate tool. When you get a result that seems significant (like any 
    number over 50), ask for user confirmation using the user_confirm tool before 
    reporting the final answer.""",
    model="claude-sonnet-4-20250514",
    thinking_tokens=1024,
    max_tokens=4096,
    tools=[calculate],  # Backend tools
    frontend_tools=[user_confirm],  # Frontend tools - executed in browser
    db_backend="filesystem",
)

print(frontend_agent)
print(f"\nFrontend tool schemas: {[t['name'] for t in frontend_agent.frontend_tool_schemas]}")
print(f"Backend tool schemas: {[t['name'] for t in frontend_agent.tool_schemas]}")


{
  "agent_uuid": "ece86ab1-24e4-4234-a89b-7629e628aae4",
  "system_prompt": "You are a helpful assistant. When asked to perform calculations,\n    use the calculate tool. When you get a result that seems significant (like any \n    number over 50), ask for user confirmation using the user_confirm tool before \n    reporting the final answer.",
  "model": "claude-sonnet-4-20250514",
  "max_steps": 50,
  "thinking_tokens": 1024,
  "max_tokens": 4096,
  "stream_meta_history_and_tool_results": false,
  "beta_headers": [],
  "container_id": null,
  "messages_count": 0,
  "conversation_history_count": 0,
  "agent_logs_count": 0,
  "max_retries": 5,
  "base_delay": 1.0,
  "api_kwargs": {},
  "formatter": "xml",
  "compactor": null,
  "memory_store": null,
  "final_answer_check": false,
  "db_backend": "FilesystemBackend",
  "tools": [
    "calculate"
  ]
}

Frontend tool schemas: ['user_confirm']
Backend tool schemas: ['calculate']


## Running Agent - Pauses for Frontend Tool

When Claude decides to use a frontend tool (like `user_confirm`), the agent:
1. Executes any backend tools first
2. Emits `<awaiting_frontend_tools data="...">` in the stream
3. Persists state to DB
4. Returns early with `stop_reason="awaiting_frontend_tools"`


In [4]:
import asyncio

prompt = "Calculate 25 * 4 for me."

# Create queue to capture streaming output
queue: asyncio.Queue[str | None] = asyncio.Queue()
collected_output = []

async def collect_output():
    while True:
        chunk = await queue.get()
        if chunk is None:
            break
        collected_output.append(chunk)
        # Print chunks that signal frontend tools
        if "awaiting_frontend_tools" in chunk:
            print(f"\n>>> FRONTEND TOOLS SIGNAL DETECTED <<<")
            print(chunk[:300] + "...")
        queue.task_done()

collector = asyncio.create_task(collect_output())

result = await frontend_agent.run(prompt, queue)

await queue.put(None)
await collector

print(f"\nStop reason: {result.stop_reason}")
print(f"Total steps: {result.total_steps}")



>>> FRONTEND TOOLS SIGNAL DETECTED <<<
<awaiting_frontend_tools data="[{&quot;tool_use_id&quot;: &quot;toolu_01RqYKsq9iZMREGTiwXF5FeG&quot;, &quot;name&quot;: &quot;user_confirm&quot;, &quot;input&quot;: {&quot;message&quot;: &quot;I calculated 25 * 4 = 100. Since this result is over 50, I want to confirm before reporting this answer. Sh...

Stop reason: awaiting_frontend_tools
Total steps: 2


In [5]:
# Inspect the paused state
print(f"Awaiting frontend tools: {frontend_agent._awaiting_frontend_tools}")
print(f"Pending frontend tools: {json.dumps(frontend_agent._pending_frontend_tools, indent=2)}")
print(f"Pending backend results: {len(frontend_agent._pending_backend_results)} results")
print(f"Current step: {frontend_agent._current_step}")


Awaiting frontend tools: True
Pending frontend tools: [
  {
    "tool_use_id": "toolu_01RqYKsq9iZMREGTiwXF5FeG",
    "name": "user_confirm",
    "input": {
      "message": "I calculated 25 * 4 = 100. Since this result is over 50, I want to confirm before reporting this answer. Should I proceed with reporting that 25 * 4 = 100?"
    }
  }
]
Pending backend results: 0 results
Current step: 2


In [6]:
# Save the UUID before "losing" the agent instance
saved_uuid = frontend_agent.agent_uuid
print(f"Saved UUID: {saved_uuid}")

# Get the pending tool info (in a real scenario this comes from the frontend)
pending_tool = frontend_agent._pending_frontend_tools[0]
tool_use_id = pending_tool["tool_use_id"]
print(f"Tool use ID: {tool_use_id}")
print(f"Tool name: {pending_tool['name']}")
print(f"Tool input: {pending_tool['input']}")


Saved UUID: ece86ab1-24e4-4234-a89b-7629e628aae4
Tool use ID: toolu_01RqYKsq9iZMREGTiwXF5FeG
Tool name: user_confirm
Tool input: {'message': 'I calculated 25 * 4 = 100. Since this result is over 50, I want to confirm before reporting this answer. Should I proceed with reporting that 25 * 4 = 100?'}


In [7]:
# Simulate re-hydration: Create new agent instance with same UUID
# (In FastAPI, this happens in the /agent/tool_results endpoint)
rehydrated_agent = AnthropicAgent(
    system_prompt=frontend_agent.system_prompt,
    model=frontend_agent.model,
    thinking_tokens=frontend_agent.thinking_tokens,
    max_tokens=frontend_agent.max_tokens,
    tools=[calculate],
    frontend_tools=[user_confirm],
    db_backend="filesystem",
    agent_uuid=saved_uuid,  # This triggers loading state from DB
)

print(f"Re-hydrated agent UUID: {rehydrated_agent.agent_uuid}")
print(f"Awaiting frontend tools: {rehydrated_agent._awaiting_frontend_tools}")
print(f"Pending frontend tools count: {len(rehydrated_agent._pending_frontend_tools)}")


Re-hydrated agent UUID: ece86ab1-24e4-4234-a89b-7629e628aae4
Awaiting frontend tools: True
Pending frontend tools count: 1


In [8]:
# Submit frontend tool results and continue the agent
# (Simulating user clicking "yes" in the browser)
frontend_results = [
    {
        "tool_use_id": tool_use_id,
        "content": "yes",  # User confirmed
        "is_error": False,
    }
]

# Create queue for continuation stream
queue2: asyncio.Queue[str | None] = asyncio.Queue()

async def print_continuation():
    while True:
        chunk = await queue2.get()
        if chunk is None:
            break
        print(chunk, end="", flush=True)
        queue2.task_done()

printer2 = asyncio.create_task(print_continuation())

# Continue the agent with frontend tool results
result2 = await rehydrated_agent.continue_with_tool_results(frontend_results, queue2)

await queue2.put(None)
await printer2

print(f"\n\nStop reason: {result2.stop_reason}")
print(f"Total steps: {result2.total_steps}")


<content-block-tool_result id="toolu_01RqYKsq9iZMREGTiwXF5FeG" name="user_confirm"><![CDATA[yes]]></content-block-tool_result><content-block-text>The calculation 25 * 4 equals **100**.</content-block-text>

Stop reason: end_turn
Total steps: 3


In [9]:
# Show the final answer
print("Final Answer:")
print(result2.final_answer)


Final Answer:
The calculation 25 * 4 equals **100**.
